## GAN 50 sqr

This notebook is modified from the keras repository: https://github.com/BAI-Yeqi/Keras-GAN/blob/master/gan/gan.py

As tested (256, 256) is too big a input, so we are using (50, 50)


In [1]:
from __future__ import print_function, division
from keras.layers import Input, Dense, Reshape, Flatten, Dropout
from keras.layers import BatchNormalization, Activation, ZeroPadding2D
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D, Conv2D
from keras.layers import  MaxPooling2D
from keras import backend as K
from keras.models import Sequential, Model
from keras.optimizers import Adam
from keras.models import load_model

import matplotlib.pyplot as plt

import sys

import numpy as np

Using TensorFlow backend.


In [2]:
X_try = np.load("drive/Colab Notebooks/Data/ChestX_8/50sqr/image_array_batch_0.npy")
X_try.shape

(2000, 50, 50)

The Training Set of MNIST got the shape 

```
(60000, 28, 28)
```



In [11]:
class GAN():
    def __init__(self):
        self.img_rows = 50 
        self.img_cols = 50
        self.channels = 1
        self.img_shape = (self.img_rows, self.img_cols, self.channels)

        optimizer = Adam(0.0002, 0.5)

        # Build and compile the discriminator
        self.discriminator = self.build_discriminator()
        self.discriminator.compile(loss='binary_crossentropy', 
            optimizer=optimizer,
            metrics=['accuracy'])

        # Build and compile the generator
        self.generator = self.build_generator()
        self.generator.compile(loss='binary_crossentropy', optimizer=optimizer)

        # The generator takes noise as input and generated imgs
        z = Input(shape=(400,))
        img = self.generator(z)

        # For the combined model we will only train the generator
        self.discriminator.trainable = False

        # The valid takes generated images as input and determines validity
        valid = self.discriminator(img)

        # The combined model  (stacked generator and discriminator) takes
        # noise as input => generates images => determines validity 
        self.combined = Model(z, valid)
        self.combined.compile(loss='binary_crossentropy', optimizer=optimizer)

    def build_generator(self):

        noise_shape = (400,)
        
        model = Sequential()


        model.add(Dense(1024, input_shape=noise_shape))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        
        model.add(Dense(2000, input_shape=noise_shape))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        
        model.add(Dense(4000))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        
        model.add(Dense(2500))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        
        model.add(Dense(np.prod(self.img_shape), activation='tanh'))
        model.add(Reshape(self.img_shape))

        model.summary()

        noise = Input(shape=noise_shape)
        img = model(noise)

        return Model(noise, img)

    def build_discriminator(self):

        img_shape = (self.img_rows, self.img_cols, self.channels)
        """
        Method 1 : CNN
        
        model = Sequential()
        model.add(Conv2D(32, kernel_size=(3, 3),
                         activation='relu',kernel_initializer='random_uniform', bias_initializer='zeros',
                         input_shape=img_shape))
        model.add(Conv2D(64, (3, 3), activation='relu',kernel_initializer='random_uniform', bias_initializer='zeros'))
        model.add(MaxPooling2D(pool_size=(2, 2)))
        model.add(Dropout(0.25))
        model.add(Conv2D(48, (4, 4), activation='relu'))
        model.add(MaxPooling2D(pool_size=(2, 2)))
        model.add(Dropout(0.25))
        model.add(Flatten())
        model.add(Dense(128, activation='relu'))
        model.add(Dropout(0.5))
        model.add(Dense(1, activation='softmax'))
        model.summary()
        """
        
        """
        Method2: Dense
        
        model = Sequential()

        model.add(Flatten(input_shape=img_shape))
        model.add(Dense(3000))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dense(1500))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dense(256))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dense(1, activation='sigmoid'))
        model.summary()
        """ 
        """
        # Method 3 : CNN (copied from CIFAR 10 example)
        model = Sequential()
        model.add(Conv2D(32, (3, 3), padding='same',
                         input_shape=img_shape))
        model.add(Activation('relu'))
        model.add(Conv2D(32, (3, 3)))
        model.add(Activation('relu'))
        model.add(MaxPooling2D(pool_size=(2, 2)))
        model.add(Dropout(0.25))

        model.add(Conv2D(64, (3, 3), padding='same'))
        model.add(Activation('relu'))
        model.add(Conv2D(64, (3, 3)))
        model.add(Activation('relu'))
        model.add(MaxPooling2D(pool_size=(2, 2)))
        model.add(Dropout(0.25))

        model.add(Flatten())
        model.add(Dense(512))
        model.add(Activation('relu'))
        model.add(Dropout(0.5))
        model.add(Dense(1))
        model.add(Activation('softmax'))
        model.summary()
        """
        # Method 4: CIFAR-10
        model = Sequential()
        model.add(Conv2D(3, (7, 7), padding="valid", strides = (1,1),
                                 input_shape=img_shape))
        model.add(Activation('relu'))

        model.add(Conv2D(3, (7, 7), padding="valid", strides = (1,1),
                                 input_shape=img_shape))
        model.add(Activation('relu'))

        model.add(Conv2D(3, (7, 7), padding="valid", strides = (1,1),
                                 input_shape=img_shape))
        model.add(Activation('relu'))

        CIFAR_model = load_model("drive/Colab Notebooks/GAN Medical Image/Models/keras_cifar10_trained_model_e2.h5")
        
        i = 0
        for layer in CIFAR_model.layers:
          layer.name = layer.name + "_" + str(i)
          model.add(layer)
          i=i+1

        model.add(Dense(1))
        model.add(Activation('sigmoid'))
        model.summary()

        
        img = Input(shape=img_shape)
        validity = model(img)

        return Model(img, validity)

    def train(self, epochs, batch_size=128, save_interval=50):

        # Load the dataset
        # (X_train, _), (_, _) = mnist.load_data()
        X_train = np.load("drive/Colab Notebooks/Data/ChestX_8/50sqr/image_array_batch_0.npy")
        
        # Rescale -1 to 1
        X_train = (X_train.astype(np.float32) - 127.5) / 127.5
        X_train = np.expand_dims(X_train, axis=3) # to resize the images array into size (2000, 50, 50, 1)
        print("X_train shape: " + str(X_train.shape))

        half_batch = int(batch_size / 2)

        for epoch in range(epochs):

            # ---------------------
            #  Train Discriminator
            # ---------------------

            # Select a random half batch of images
            idx = np.random.randint(0, X_train.shape[0], half_batch) 
            # idx is an array of length = half_batch and value in range of the no. of training samples
            imgs = X_train[idx] # imgs are then selected from the X_train

            noise = np.random.normal(0, 1, (half_batch, 400))

            # Generate a half batch of new images
            gen_imgs = self.generator.predict(noise) # shape: (half_batch, 50, 50)

            # Train the discriminator (and the loss will be returned)
            d_loss_real = self.discriminator.train_on_batch(imgs, np.ones((half_batch, 1)))
            d_loss_fake = self.discriminator.train_on_batch(gen_imgs, np.zeros((half_batch, 1)))
            d_loss = 0.5 * np.add(d_loss_real, d_loss_fake)


            # ---------------------
            #  Train Generator
            # ---------------------

            noise = np.random.normal(0, 1, (batch_size, 400))

            # The generator wants the discriminator to label the generated samples
            # as valid (ones) (128 numbers of 1s contained in the 1 d array)
            valid_y = np.array([1] * batch_size)
            
            print("valid_y: " + str(valid_y))

            # Train the generator
            g_loss = self.combined.train_on_batch(noise, valid_y)

            # Plot the progress
            print ("%d [D loss: %f, acc.: %.2f%%] [G loss: %f]" % (epoch, d_loss[0], 100*d_loss[1], g_loss))

            # If at save interval => save generated image samples
            if epoch % save_interval == 0:
                self.save_imgs(epoch)

    def save_imgs(self, epoch):
        r, c = 5, 5
        noise = np.random.normal(0, 1, (r * c, 400))
        print("shape of noise: "+ str(noise.shape))
        gen_imgs = self.generator.predict(noise)

        # Rescale images 0 - 1
        gen_imgs = 0.5 * gen_imgs + 0.5

        fig, axs = plt.subplots(r, c)
        cnt = 0
        for i in range(r):
            for j in range(c):
                axs[i,j].imshow(gen_imgs[cnt, :,:,0], cmap='gray')
                axs[i,j].axis('off')
                cnt += 1
        fig.savefig("drive/Colab Notebooks/GAN Medical Image/Images Gen/Images GAN D-CNN FirApt/mnist_%d.png" % epoch)
        plt.close()


if __name__ == '__main__':
    gan = GAN()
    gan.train(epochs=30000, batch_size=32, save_interval=200)

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d_13 (Conv2D)           (None, 44, 44, 3)         150       
_________________________________________________________________
activation_16 (Activation)   (None, 44, 44, 3)         0         
_________________________________________________________________
conv2d_14 (Conv2D)           (None, 38, 38, 3)         444       
_________________________________________________________________
activation_17 (Activation)   (None, 38, 38, 3)         0         
_________________________________________________________________
conv2d_15 (Conv2D)           (None, 32, 32, 3)         444       
_________________________________________________________________
activation_18 (Activation)   (None, 32, 32, 3)         0         
_________________________________________________________________
conv2d_1_0 (Conv2D)          (None, 32, 32, 32)        896       
__________

/usr/local/lib/python3.6/dist-packages/keras/engine/training.py:973: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
0 [D loss: 0.729154, acc.: 50.00%] [G loss: 0.889062]
shape of noise: (25, 400)
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
1 [D loss: 0.720344, acc.: 50.00%] [G loss: 0.887333]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
2 [D loss: 0.715209, acc.: 50.00%] [G loss: 0.878017]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
3 [D loss: 0.711875, acc.: 50.00%] [G loss: 0.868224]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
4 [D loss: 0.706854, acc.: 50.00%] [G loss: 0.859740]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
5 [D loss: 0.706897, acc.: 50.00%] [G loss: 0.853201]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
6 [D loss: 0.703458, acc.: 50.00%] [G loss: 0.850063]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1

valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
58 [D loss: 0.448138, acc.: 100.00%] [G loss: 1.093766]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
59 [D loss: 0.447990, acc.: 100.00%] [G loss: 1.093939]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
60 [D loss: 0.447840, acc.: 100.00%] [G loss: 1.094229]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
61 [D loss: 0.447725, acc.: 100.00%] [G loss: 1.094456]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
62 [D loss: 0.447552, acc.: 100.00%] [G loss: 1.094643]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
63 [D loss: 0.447410, acc.: 100.00%] [G loss: 1.094899]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
64 [D loss: 0.447274, acc.: 100.00%] [G loss: 1.094827]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
65 [D lo

valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
118 [D loss: 0.440192, acc.: 100.00%] [G loss: 1.107009]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
119 [D loss: 0.440067, acc.: 100.00%] [G loss: 1.107222]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
120 [D loss: 0.439941, acc.: 100.00%] [G loss: 1.107437]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
121 [D loss: 0.439815, acc.: 100.00%] [G loss: 1.107646]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
122 [D loss: 0.439690, acc.: 100.00%] [G loss: 1.107863]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
123 [D loss: 0.439564, acc.: 100.00%] [G loss: 1.108075]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
124 [D loss: 0.439439, acc.: 100.00%] [G loss: 1.108268]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
1

...

29713 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693888]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29714 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693888]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29715 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693888]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29716 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693888]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29717 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693887]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29718 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693887]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29719 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693887]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29720 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693887]
valid_y: [1

29773 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693874]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29774 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693874]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29775 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693873]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29776 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693873]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29777 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693873]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29778 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693873]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29779 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693873]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29780 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693872]
valid_y: [1

valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29833 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693860]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29834 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693859]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29835 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693859]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29836 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693859]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29837 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693859]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29838 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693858]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29839 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693858]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1

valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29893 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693845]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29894 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693845]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29895 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693845]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29896 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693845]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29897 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693844]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29898 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693844]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29899 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693844]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1

valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29953 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693831]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29954 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693831]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29955 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693830]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29956 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693830]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29957 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693830]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29958 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693830]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
29959 [D loss: 0.693181, acc.: 50.00%] [G loss: 0.693830]
valid_y: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1

In [1]:
!apt-get install -y -qq software-properties-common python-software-properties module-init-tools
!add-apt-repository -y ppa:alessandro-strada/ppa 2>&1 > /dev/null
!apt-get update -qq 2>&1 > /dev/null
!apt-get -y install -qq google-drive-ocamlfuse fuse
from google.colab import auth
auth.authenticate_user()
from oauth2client.client import GoogleCredentials
creds = GoogleCredentials.get_application_default()
import getpass
!google-drive-ocamlfuse -headless -id={creds.client_id} -secret={creds.client_secret} < /dev/null 2>&1 | grep URL
vcode = getpass.getpass()
!echo {vcode} | google-drive-ocamlfuse -headless -id={creds.client_id} -secret={creds.client_secret}

Please, open the following URL in a web browser: https://accounts.google.com/o/oauth2/auth?client_id=32555940559.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive&response_type=code&access_type=offline&approval_prompt=force
··········
Please, open the following URL in a web browser: https://accounts.google.com/o/oauth2/auth?client_id=32555940559.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive&response_type=code&access_type=offline&approval_prompt=force
Please enter the verification code: Access token retrieved correctly.


In [0]:
!mkdir -p drive
!google-drive-ocamlfuse drive
!pip install -q keras

In [2]:
from tensorflow.python.client import device_lib
device_lib.list_local_devices()

[name: "/device:CPU:0"
 device_type: "CPU"
 memory_limit: 268435456
 locality {
 }
 incarnation: 944791236682169329, name: "/device:GPU:0"
 device_type: "GPU"
 memory_limit: 10958117274
 locality {
   bus_id: 1
 }
 incarnation: 9015535233609563456
 physical_device_desc: "device: 0, name: Tesla K80, pci bus id: 0000:00:04.0, compute capability: 3.7"]

In [6]:
import numpy as np
batch_size = 128
valid_y = np.array([1] * batch_size)
valid_y

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1])

### here we are testing how to employ the existing models (from CIFAR 10)

In [0]:
from keras.models import load_model

In [7]:
CIFAR_model = load_model("drive/Colab Notebooks/GAN Medical Image/Models/keras_cifar10_trained_model_e2.h5")
print(CIFAR_model.layers)
CIFAR_model.summary()

[<keras.layers.convolutional.Conv2D object at 0x7f37cc5a38d0>, <keras.layers.core.Activation object at 0x7f37cc5a3b70>, <keras.layers.convolutional.Conv2D object at 0x7f37cc5a3a58>, <keras.layers.core.Activation object at 0x7f37cc5ae438>, <keras.layers.pooling.MaxPooling2D object at 0x7f37cc5a3b38>, <keras.layers.core.Dropout object at 0x7f381ffa86a0>, <keras.layers.convolutional.Conv2D object at 0x7f37cc6efa58>, <keras.layers.core.Activation object at 0x7f380e725978>, <keras.layers.convolutional.Conv2D object at 0x7f37cde71d30>, <keras.layers.core.Activation object at 0x7f37cde51a90>, <keras.layers.pooling.MaxPooling2D object at 0x7f37ccdf4b38>, <keras.layers.core.Dropout object at 0x7f37ccde92b0>, <keras.layers.core.Flatten object at 0x7f37ccde9ac8>, <keras.layers.core.Dense object at 0x7f37ccde0a20>, <keras.layers.core.Activation object at 0x7f37cce2b668>, <keras.layers.core.Dropout object at 0x7f37cce2b710>, <keras.layers.core.Dense object at 0x7f37ccde9b70>, <keras.layers.core.Act

In [8]:
CIFAR_model.layers[0: -3]

In [10]:
img_shape = (50, 50, 1)

model = Sequential()
model.add(Conv2D(3, (7, 7), padding="valid", strides = (1,1),
                         input_shape=img_shape))
model.add(Activation('relu'))

model.add(Conv2D(3, (7, 7), padding="valid", strides = (1,1),
                         input_shape=img_shape))
model.add(Activation('relu'))

model.add(Conv2D(3, (7, 7), padding="valid", strides = (1,1),
                         input_shape=img_shape))
model.add(Activation('relu'))

i = 0
for layer in CIFAR_model.layers:
  layer.name = layer.name + str(i)
  model.add(layer)
  i=i+1

model.add(Dense(1))
model.add(Activation('sigmoid'))
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d_10 (Conv2D)           (None, 44, 44, 3)         150       
_________________________________________________________________
activation_12 (Activation)   (None, 44, 44, 3)         0         
_________________________________________________________________
conv2d_11 (Conv2D)           (None, 38, 38, 3)         444       
_________________________________________________________________
activation_13 (Activation)   (None, 38, 38, 3)         0         
_________________________________________________________________
conv2d_12 (Conv2D)           (None, 32, 32, 3)         444       
_________________________________________________________________
activation_14 (Activation)   (None, 32, 32, 3)         0         
_________________________________________________________________
00 (Conv2D)                  (None, 32, 32, 32)        896       
__________